In [1]:
import time
import numpy as np
import pandas as pd
import requests

import json
from pandas.io.json import json_normalize

In [2]:
import _local_settings

In [3]:
# Set ipython's max row display
pd.set_option('display.max_row', 1000)

# Set iPython's max column width to 50
pd.set_option('display.max_columns', 50)

### Get Data Directly from Steam

In [4]:
ALL_APPS_URL = "http://api.steampowered.com/ISteamApps/GetAppList/v0002/?key=STEAMKEY&format=json"
APP_DETAILS_URL = "http://store.steampowered.com/api/appdetails?appids={APP_ID}"

In [5]:
def get_request(url, parameters=None):
    """Return json-formatted response of a get request using optional parameters.

    Parameters
    ----------
    url : string
    parameters : {'parameter': 'value'}
        parameters to pass as part of get request

    Returns
    -------
    json_data
        json-formatted response (dict-like)
    """
    try:
        response = requests.get(url=url, params=parameters)
    except requests.exceptions.Timeout:
        for i in range(5, 0, -1):
            print('\rTimeout. Waiting... ({})'.format(i), end='')
            time.sleep(1)
        print('\rRetrying.' + ' ' * 10)
        return get_request(url, parameters)
    except requests.exceptions.TooManyRedirects:
        print('TooManyRedirects')
    except requests.exceptions.RequestException as e:
    # catastrophic error. bail.
        raise SystemExit(e)

    if response:
        return response.json()
    else:
        # response is none usually means too many requests. Wait and try again
        print('No response, waiting 10 seconds...')
        time.sleep(10)
        print('Retrying.')
        return get_request(url, parameters)

In [6]:
ALL_APPS_URL = "http://api.steampowered.com/ISteamApps/GetAppList/v0002/?key={STEAMKEY}&format=json".format(STEAMKEY=_local_settings.STEAMKEY)

all_apps = get_request(ALL_APPS_URL)

In [7]:
print(list(all_apps['applist']['apps'])[0:25])

[]


In [10]:
def get_app_info(apps):
# needs logic to deal with 200 requests/5 min limits
    count = 0
    loop_count = 0
    failure = 0
    success = 0
    app_data = {}
    app_failure = {}
    for app in apps:
        appid = app['appid']
        count+= 1
        app_info = get_request("http://store.steampowered.com/api/appdetails?appids={APP_ID}".format(APP_ID=appid))
        time.sleep(1.6)  # should keep us below request limit

        if app_info[str(appid)]['success']:
            success += 1
            app_data.update(app_info)
#             app_df.to_csv('initial.csv', index=False) 
        else:
            failure += 1
            app_failure.update(app_info)
#             app_failure_df.to_csv('app_failure.csv', index=False) 
        
        print(str(count))
        if count > 5:
            print("reached 2,000 request, stopping")
            break

    print('success: ' + str(success))
    print('failures: ' + str(failure))
    return app_data, app_failure

app_data, app_failure = get_app_info(all_apps['applist']['apps'])






1
2
3
4
5
6
reached 2,000 request, stopping
success: 3
failures: 3


In [11]:
def convert_to_df(d):
    df = pd.DataFrame.from_dict(d, orient='index')
    df.reset_index(level=0, inplace=True)
    return df

app_df = convert_to_df(app_failure)


print(app_df)

    index  success
0  216938    False
1  660010    False
2  660130    False


In [12]:
from sqlalchemy import create_engine
engine = create_engine('sqlite://', echo=False)

app_df.to_sql('failure', con=engine)
engine.execute("SELECT * FROM failure").fetchall()

[(0, '216938', 0), (1, '660010', 0), (2, '660130', 0)]

In [14]:
app_df_success = convert_to_df(app_data)
app_df_success = app_df_success.set_index('index')

df = pd.concat([app_df_success.drop(['data'], axis=1), app_df_success['data'].apply(pd.Series)], axis=1)
print(df.info())
del_cols = [#'index',
        'success',
        'header_image',
        'pc_requirements',
        'mac_requirements',
        'linux_requirements',
        'support_info',
        'background',
        #'legal_notice',
#         'reviews',
        'content_descriptors']

num_type_list = ['required_age']

rename_dict = {
    'name': 'game_name'
}

# set steam_appid as index
df.set_index('steam_appid')

# remove columns we don't care about
df_clean = df.drop(columns=del_cols, axis=1)

# rename columns as appropriate
df_clean.rename(columns=rename_dict, inplace=True)

df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3 entries, 908227 to 908240
Data columns (total 33 columns):
 #   Column                Non-Null Count  Dtype 
---  ------                --------------  ----- 
 0   success               3 non-null      bool  
 1   type                  3 non-null      object
 2   name                  3 non-null      object
 3   steam_appid           3 non-null      int64 
 4   required_age          3 non-null      int64 
 5   is_free               3 non-null      bool  
 6   detailed_description  3 non-null      object
 7   about_the_game        3 non-null      object
 8   short_description     3 non-null      object
 9   fullgame              2 non-null      object
 10  supported_languages   3 non-null      object
 11  header_image          3 non-null      object
 12  website               2 non-null      object
 13  pc_requirements       3 non-null      object
 14  mac_requirements      3 non-null      object
 15  linux_requirements    3 non-null      o

In [15]:
from sqlalchemy import create_engine
engine = create_engine('sqlite://', echo=False)

df.to_sql('test', con=engine)
engine.execute("SELECT * FROM test").fetchall()

InterfaceError: (sqlite3.InterfaceError) Error binding parameter 10 - probably unsupported type.
[SQL: INSERT INTO test ("index", success, type, name, steam_appid, required_age, is_free, detailed_description, about_the_game, short_description, fullgame, supported_languages, header_image, website, pc_requirements, mac_requirements, linux_requirements, legal_notice, developers, publishers, price_overview, packages, package_groups, platforms, categories, genres, screenshots, release_date, support_info, background, content_descriptors, dlc, movies, achievements) VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)]
[parameters: (('908227', 1, 'dlc', 'Pinball Arcade: Doctor Who Master of Time', 908227, 0, 0, 'This includes the Doctor Who: Master of Time Pinball table (individual table)', 'This includes the Doctor Who: Master of Time Pinball table (individual table)', 'This includes the Doctor Who: Master of Time Pinball table (individ

In [ ]:
app_failure_df = convert_to_df(app_failure)
# app_failure_df.to_csv('app_failure.csv', index=False) 

In [16]:
# app_df = pd.read_csv('initial.csv')

# app_df.head()

app_df.loc['147283']

KeyError: '147283'

In [17]:
app_df_expanded = pd.concat([app_df.drop(['data'], axis=1), app_df['data'].apply(pd.Series)], axis=1)

KeyError: "['data'] not found in axis"

In [ ]:
app_df_expanded[['type','name','price_overview']]

In [ ]:
app_df_expanded.info()

### Get SteamSpy data - do we really want or need it? - eitherr way we shop rows we don't care about in Steam data...

In [ ]:
def get_streamspy_info(apps):
    count = 0
    app_data = []
    url = "https://steamspy.com/api.php"
    
    
    for app in apps:
        count+= 1
        print(app)
        parameters = {"request": "appdetails", "appid": app}
        app_info = get_request(url, parameters)
        time.sleep(.3)  # should keep us below request limit
        app_data.append(app_info)

    print("Found " + str(count) + " apps on SteamSpy.")
    return app_data

# sp_app_data = get_streamspy_info(app_df_expanded['index'])
sp_app_data = get_streamspy_info(all_apps['applist']['apps'])



{'appid': 216938, 'name': 'Pieterw test app76 ( 216938 )'}
{'appid': 660010, 'name': 'test2'}
{'appid': 660130, 'name': 'test3'}
{'appid': 908227, 'name': 'Pinball Arcade: Doctor Who Master of Time'}
{'appid': 908230, 'name': 'Basketball Hoop'}


In [ ]:
sp_app_data_df = pd.DataFrame(sp_app_data)
# sp_app_data_df.to_csv('steamspy_raw.csv', index=False) 

In [ ]:
sp_app_data_df

### Play with Steam Data to tease out anything useful / not useful

In [ ]:
app_df_expanded.head()

In [ ]:
app_df_expanded.info()

In [ ]:
app_df_expanded.drm_notice.unique()


### Data modifications to make to Steam Data

(x) remove rows with types not equal to game, dlc or demo  
(x) remove 'index' column and make the steam_appid column the index.  they are always equal.  
(x) remove mac/pc/linux requirements as we can use the platforms column to determine what is supported - dont care about specifics  
(x) change required_age to int type  
(x) need to flatten the price_overview column - are they all formatted the same so I could split it into 2?  
(x) split platforms column into 3 (Windows, Mac, Linux) bool columns  
(x) recommendations should pull out just the number and convert column to int  
(x) convert controller support so bool -> [nan, 'full'] == [False, True]  
(x) convert screenshots to just a counter of number of screenshots  
(x) convert movie to just a counter of number of movies - doesnt look like we can get the movie length from this data  
(x) split out the genres column so that we can easily access them - probably need to get a list of all genres  
(x) convert release_data to a date, if 'coming_soon==True' set a flag for not release? maybe a new column?  
(x) review column is just one review - not useful so delete  
(x) pull out the appid of the fullgame column so we can link them if needed  
(x) demos is link to appids for game demo - my data sample only has a single demo per game so i just pulled out that id for now - will have to update this code if we find some games with multiple demos  
(x) dlc is a list of appids for dlc - kept this column as is an added another column (dlc_count) that is just number of dlc appids  
(x) split out categories column so they can be easily accessed  
(x) pulled out metacritic score and dropped correspdoning URL  
(x) content descriptors relates to age_restrictions - since >18 games are not relevant to us i dropped this column  
(x) converted achievements to just a count of the game acheievements  
(x) columns to remove  
    - index
    - header_image
    - pc_requirements
    - mac_requirements
    - linux_requirements 
    - content descriptors 
    - support_info
    - background
    - legal notice 
    - reviews 

standing questions:
- can i drop all games with an age restriction?- find out if drm_notice, ext_user_account_notice mean anything to Kyle?  Short list of values.
- define the packages and package_group column? list of a numeric? looks like appids but they dont (all) map back to anything relevant?  but maybe it's just because i dont have the entire pool


In [583]:
# set steam_appid as index
app_df_expanded.set_index('steam_appid')

# remove columns we don't care about
cols = ['index',
        'success',
        'header_image',
        'pc_requirements',
        'mac_requirements',
        'linux_requirements',
        'content_descriptors',
        'support_info',
        'background',
        'legal_notice',
        'reviews']

app_df_cleaned_1 = app_df_expanded.drop(columns=cols, axis=1)
app_df_cleaned_1.rename(columns={'name': 'game_name'}, inplace=True)

app_df_cleaned_1.head()


type                                       name  steam_appid required_age  \
0   game                                   Swatcher       579920            0   
1    dlc  Secret World Legends: Supernatural Bundle       579930            0   
2   game                        Race for the Galaxy       579940            0   
3  music     Milkmaid of the Milky Way - Soundtrack       579960            0   
4   demo                         Don't Mess Up Demo       579970            0   

   is_free                               detailed_description  \
0    False  Swatcher is a color palette creation tool with...   
1    False  <h1>Secret World Legends</h1><p>Secret World L...   
2    False  Explore, Develop, Settle, Trade, Consume, or P...   
3    False  This is the Official Soundtrack for Milkmaid o...   
4     True  Don't Mess Up is a collection of VR minigames ...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
3  This is the Official Soundtrack for Milkmaid o...   
4  Don't Mess Up is a collection of VR minigames ...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
3  The relaxing and soothing Official Soundtrack ...   
4  Don't Mess Up is a collection of VR minigames ...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
3                                            English   
4  English<strong>*</strong><br><strong>*</strong...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
3          http://milkmaidgame.com    [Mattis Folkestad]   
4                             None            [OKatBest]   

             publishers                                     price_overview  \
0        [Frozen Flame]  {'currency': 'USD', 'initial': 499, 'final': 4...   
1              [Funcom]  {'currency': 'USD', 'initial': 5999, 'final': ...   
2  [Temple Gates Games]  {'currency': 'USD', 'initial': 699, 'final': 6...   
3          [machineboy]  {'currency': 'USD', 'initial': 199, 'final': 1...   
4            [OKatBest]                                                NaN   

   packages                                     package_groups  \
0  [148602]  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [148605]  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [148608]  [{'name': 'default', 'title': 'Buy Race for th...   
3  [148614]  [{'name': 'default', 'title': 'Buy Milkmaid of...   
4       NaN                                                 []   

                                         platforms  \
0  {'windows': True, 'mac': False, 'linux': False}   
1  {'windows': True, 'mac': False, 'linux': False}   
2  {'windows': True, 'mac': False, 'linux': False}   
3   {'windows': True, 'mac': True, 'linux': False}   
4  {'windows': True, 'mac': False, 'linux': False}   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
3  [{'id': '25', 'description': 'Adventure'}, {'i...   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
3 

In [584]:
# remove rows with types not equal to game, dlc or demo
print(app_df_cleaned_1.type.unique())
valid_type = ['game', 'dlc', 'demo']

contains = [app_df_cleaned_1['type'].str.contains(i) for i in valid_type]
app_df_cleaned_2 = app_df_cleaned_1[np.any(contains, axis=0)]
app_df_cleaned_2.head()
# app_df_cleaned_2 = app_df_cleaned_1[app_df_cleaned_1['type'] == 'music']

['game' 'dlc' 'music' 'demo' 'video' 'episode' 'series']


type                                       name  steam_appid required_age  \
0  game                                   Swatcher       579920            0   
1   dlc  Secret World Legends: Supernatural Bundle       579930            0   
2  game                        Race for the Galaxy       579940            0   
4  demo                         Don't Mess Up Demo       579970            0   
5  game                                  Lost Eden       579980            0   

   is_free                               detailed_description  \
0    False  Swatcher is a color palette creation tool with...   
1    False  <h1>Secret World Legends</h1><p>Secret World L...   
2    False  Explore, Develop, Settle, Trade, Consume, or P...   
4     True  Don't Mess Up is a collection of VR minigames ...   
5    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers                                     price_overview  \
0        [Frozen Flame]  {'currency': 'USD', 'initial': 499, 'final': 4...   
1              [Funcom]  {'currency': 'USD', 'initial': 5999, 'final': ...   
2  [Temple Gates Games]  {'currency': 'USD', 'initial': 699, 'final': 6...   
4            [OKatBest]                                                NaN   
5           [Interplay]  {'currency': 'USD', 'initial': 999, 'final': 9...   

   packages                                     package_groups  \
0  [148602]  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [148605]  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [148608]  [{'name': 'default', 'title': 'Buy Race for th...   
4       NaN                                                 []   
5  [148620]  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                         platforms  \
0  {'windows': True, 'mac': False, 'linux': False}   
1  {'windows': True, 'mac': False, 'linux': False}   
2  {'windows': True, 'mac': False, 'linux': False}   
4  {'windows': True, 'mac': False, 'linux': False}   
5  {'windows': True, 'mac': False, 'linux': False}   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
4  [{'i

In [585]:
# change required_age to int type

app_df_cleaned_2['required_age'] = pd.to_numeric(app_df_cleaned_2['required_age'])

app_df_cleaned_2.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 30 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   type                     697 non-null    object
 1   name                     697 non-null    object
 2   steam_appid              697 non-null    int64 
 3   required_age             697 non-null    int64 
 4   is_free                  697 non-null    bool  
 5   detailed_description     697 non-null    object
 6   about_the_game           697 non-null    object
 7   short_description        697 non-null    object
 8   supported_languages      694 non-null    object
 9   website                  503 non-null    object
 10  developers               696 non-null    object
 11  publishers               697 non-null    object
 12  price_overview           569 non-null    object
 13  packages                 573 non-null    object
 14  package_groups           697 non-null    o

/Users/emily/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [586]:
# need to flatten the price_overview column - are they all formatted the same so I could split it into 2?

app_df_cleaned_3 = app_df_cleaned_2.copy()

# s = app_df_cleaned_3['price_overview'].apply(pd.Series)
# s.drop(axis=1, columns=['final_formatted', 'initial_formatted'], inplace=True)
# s['final'] = s['final'] / 100
# s['initial'] = s['initial'] / 100
# s.head()

app_df_cleaned_3 = pd.concat([app_df_cleaned_3, app_df_cleaned_3['price_overview'].apply(pd.Series)], axis=1)
app_df_cleaned_3.drop(axis=1, columns='price_overview', inplace=True)
app_df_cleaned_3.drop(axis=1, columns=[0, 'final_formatted', 'initial_formatted'], inplace=True)
app_df_cleaned_3['final'] = app_df_cleaned_3['final'] / 100
app_df_cleaned_3['initial'] = app_df_cleaned_3['initial'] / 100

app_df_cleaned_3.rename(columns={'currency': 'price_currency',
                                 'discount_percent': 'price_discount_percent', 
                                 'final': 'price_final', 
                                 'initial': 'price_initial',
                                 'recurring_sub': 'price_recurring_sub',
                                 'recurring_sub_desc': 'price_recurring_sub_desc'}, inplace=True)


app_df_cleaned_3.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 35 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   type                      697 non-null    object 
 1   name                      697 non-null    object 
 2   steam_appid               697 non-null    int64  
 3   required_age              697 non-null    int64  
 4   is_free                   697 non-null    bool   
 5   detailed_description      697 non-null    object 
 6   about_the_game            697 non-null    object 
 7   short_description         697 non-null    object 
 8   supported_languages       694 non-null    object 
 9   website                   503 non-null    object 
 10  developers                696 non-null    object 
 11  publishers                697 non-null    object 
 12  packages                  573 non-null    object 
 13  package_groups            697 non-null    object 
 14  platforms 

In [587]:
# Split platforms into 3 bool columns
app_df_cleaned_4 = app_df_cleaned_3.copy()


app_df_cleaned_4 = pd.concat([app_df_cleaned_4, app_df_cleaned_4['platforms'].apply(pd.Series)], axis=1)
app_df_cleaned_4.drop(axis=1, columns='platforms', inplace=True)
app_df_cleaned_4.rename(columns={'windows': 'windows_support', 'mac': 'mac_support', 'linux': 'linux_support'}, inplace=True)
app_df_cleaned_4.head()

type                                       name  steam_appid  required_age  \
0  game                                   Swatcher       579920             0   
1   dlc  Secret World Legends: Supernatural Bundle       579930             0   
2  game                        Race for the Galaxy       579940             0   
4  demo                         Don't Mess Up Demo       579970             0   
5  game                                  Lost Eden       579980             0   

   is_free                               detailed_description  \
0    False  Swatcher is a color palette creation tool with...   
1    False  <h1>Secret World Legends</h1><p>Secret World L...   
2    False  Explore, Develop, Settle, Trade, Consume, or P...   
4     True  Don't Mess Up is a collection of VR minigames ...   
5    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
4  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
5  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   

                                              movies  \
0  [{'id': 256677722, 'name': 'Swatcher Demonstra...   
1  [{'id': 256691734, 'name': 'Trailer', 'thumbna...   
2  [{'id': 256687045, 'name': 'Race for the Galax...   
4                                                NaN   
5  [{'id': 256679159, 'name': 'game play trailer'...   

                                     release_date  \
0  {'coming_soon': False, 'date': 'Jan 13, 2017'}   
1  {'coming_soon': False, 'date': 'Jul 31, 2017'}   
2  {'coming_soon': Fals

In [588]:
# recommendations should pull out just the number and convert column to int
app_df_cleaned_5 = app_df_cleaned_4.copy()

app_df_cleaned_5 = pd.concat([app_df_cleaned_5, app_df_cleaned_5['recommendations'].apply(pd.Series)], axis=1)
app_df_cleaned_5.drop(axis=1, columns=[0, 'recommendations'], inplace=True)
app_df_cleaned_5.rename(columns={'total': 'recommendations'}, inplace=True)
app_df_cleaned_5.head()

type                                       name  steam_appid  required_age  \
0  game                                   Swatcher       579920             0   
1   dlc  Secret World Legends: Supernatural Bundle       579930             0   
2  game                        Race for the Galaxy       579940             0   
4  demo                         Don't Mess Up Demo       579970             0   
5  game                                  Lost Eden       579980             0   

   is_free                               detailed_description  \
0    False  Swatcher is a color palette creation tool with...   
1    False  <h1>Secret World Legends</h1><p>Secret World L...   
2    False  Explore, Develop, Settle, Trade, Consume, or P...   
4     True  Don't Mess Up is a collection of VR minigames ...   
5    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                         screenshots  \
0  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
1  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
2  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
4  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   
5  [{'id': 0, 'path_thumbnail': 'https://steamcdn...   

                                              movies  \
0  [{'id': 256677722, 'name': 'Swatcher Demonstra...   
1  [{'id': 256691734, 'name': 'Trailer', 'thumbna...   
2  [{'id': 256687045, 'name': 'Race for the Galax...   
4                                                NaN   
5  [{'id': 256679159, 'name': 'game play trailer'...   

                                     release_date  \
0  {'coming_soon': False, 'date': 'Jan 13, 2017'}   
1  {'coming_soon': False, 'date': 'Jul 31, 2017'}   
2  {'coming_soon': Fals

In [589]:
# convert controller support so bool
app_df_cleaned_6 = app_df_cleaned_5.copy()

app_df_cleaned_6['controller_support'] = app_df_cleaned_6['controller_support'].map({np.nan: False, 'full': True})
app_df_cleaned_6.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 37 columns):
 #   Column                    Non-Null Count  Dtype  
---  ------                    --------------  -----  
 0   type                      697 non-null    object 
 1   name                      697 non-null    object 
 2   steam_appid               697 non-null    int64  
 3   required_age              697 non-null    int64  
 4   is_free                   697 non-null    bool   
 5   detailed_description      697 non-null    object 
 6   about_the_game            697 non-null    object 
 7   short_description         697 non-null    object 
 8   supported_languages       694 non-null    object 
 9   website                   503 non-null    object 
 10  developers                696 non-null    object 
 11  publishers                697 non-null    object 
 12  packages                  573 non-null    object 
 13  package_groups            697 non-null    object 
 14  genres    

In [590]:
# convert screenshots and movie to just a counter of number of movies 
# doesnt look like we can get the movie length from this data

def replace_with_count(df, col):
    df = pd.concat([df, df[col].str.len()], axis=1)
    # this results in both old and new columns having the same name 
    # so below code will remove the old screenshots dictionary column
    df = df.loc[:,~df.columns.duplicated(keep='last')]
    return df

app_df_cleaned_7 = app_df_cleaned_6.copy()

app_df_cleaned_7 = replace_with_count(app_df_cleaned_7, 'screenshots')
app_df_cleaned_7.rename(columns={'screenshots': 'screenshot_count'}, inplace=True)


app_df_cleaned_7 = replace_with_count(app_df_cleaned_7, 'movies')
app_df_cleaned_7.rename(columns={'movies': 'movie_count'}, inplace=True)

app_df_cleaned_7.head()

type                                       name  steam_appid  required_age  \
0  game                                   Swatcher       579920             0   
1   dlc  Secret World Legends: Supernatural Bundle       579930             0   
2  game                        Race for the Galaxy       579940             0   
4  demo                         Don't Mess Up Demo       579970             0   
5  game                                  Lost Eden       579980             0   

   is_free                               detailed_description  \
0    False  Swatcher is a color palette creation tool with...   
1    False  <h1>Secret World Legends</h1><p>Secret World L...   
2    False  Explore, Develop, Settle, Trade, Consume, or P...   
4     True  Don't Mess Up is a collection of VR minigames ...   
5    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                              genres  \
0  [{'id': '53', 'description': 'Design & Illustr...   
1  [{'id': '1', 'description': 'Action'}, {'id': ...   
2           [{'id': '2', 'description': 'Strategy'}]   
4  [{'id': '1', 'description': 'Action'}, {'id': ...   
5  [{'id': '25', 'description': 'Adventure'}, {'i...   

                                     release_date  \
0  {'coming_soon': False, 'date': 'Jan 13, 2017'}   
1  {'coming_soon': False, 'date': 'Jul 31, 2017'}   
2  {'coming_soon': False, 'date': 'Jun 27, 2017'}   
4  {'coming_soon': False, 'date': 'Jan 13, 2017'}   
5  {'coming_soon': False, 'date': 'Feb 13, 2017'}   

                                            fullgame  \
0                                                NaN   
1  {'appid': '215280', 'name': 'Secret World Lege...   
2                                                NaN   
4       {'appid': '575170', 'name': 'Don't Mess Up'}   
5                                                NaN   

                                          categories  \
0                                                NaN   
1  [{'id': 1, 'description': 'Multi-player'}, {'i...   
2  [{'id': 2, 'description': 'Si

In [591]:
# split out the genres column so that we can easily access them - probably need to get a list of all genres
app_df_cleaned_8 = app_df_cleaned_7.copy()

#first we need to create a table of all possible values then figure out how to store those so we can access them
s = app_df_cleaned_8['genres'].apply(pd.Series)
# combine everything into single column
y = s[0].append([s[1],s[2],s[3],s[4],s[5],s[6],s[7],s[8],s[9]],ignore_index=True).dropna()
#split out dict to seprate columns
z = y.apply(pd.Series)
z = z.drop_duplicates(subset=['id','description'], keep="first")

# create a column for each unique genre and then fill those columns in the df with bools
for index, row in z.iterrows():
    no_space_name = row['description'].replace(" ", "_")
    new_col = 'genre_{}'.format(no_space_name)
    app_df_cleaned_8[new_col] = False

for index, row in app_df_cleaned_8.iterrows():
    if type(row['genres']) == float:
        continue
    for item in row['genres']:
        no_space_name = item['description'].replace(" ", "_")
        new_name = 'genre_{}'.format(no_space_name)
        app_df_cleaned_8.at[index, new_name] = True

app_df_cleaned_8.drop(columns='genres', inplace=True)
app_df_cleaned_8

type                                               name  steam_appid  \
0    game                                           Swatcher       579920   
1     dlc          Secret World Legends: Supernatural Bundle       579930   
2    game                                Race for the Galaxy       579940   
4    demo                                 Don't Mess Up Demo       579970   
5    game                                          Lost Eden       579980   
6     dlc                             TEKKEN 7 - Season Pass       580020   
7    game                                            Formata       580040   
8     dlc            RPG Maker MV - Elemental Dungeons Tiles       580050   
9     dlc                   RPG Maker MV - Future Steam Punk       580051   
10   game                                     Cut Cut Buffet       580060   
11   demo                                      Frog Hop Demo       580070   
12    dlc         RPG Maker MV - Add-on Vol.3: Train Tileset       580080   
13    dlc   RPG Maker MV - Add-on Vol.4: Kid Generator Parts       580081   
14    dlc                Darkest Dungeon®: The Crimson Court       580100   
15   demo                                  Abyssal Zone Demo       580110   
16    dlc                                Westboro Soundtrack       580120   
17    dlc                                  Laraan SoundTrack       580160   
18   game                                 My Lovely Daughter       580170   
19   game               Yonder: The Cloud Catcher Chronicles       580200   
20    dlc                                  真恋～寄语枫秋～特色作曲家（秋石）       580210   
21    dlc       Fantasy Grounds - More Monsters (Token Pack)       580240   
22   demo                     Crypt of the Serpent King Demo       580250   
24    dlc                 Fantasy Grounds - Black Magic (5E)       580290   
25   game                                 Super Stone Legacy       580300   
26   game                                           Ashworld       580320   
27    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579531   
28    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579532   
29    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579533   
30    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579534   
31    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579535   
32    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579536   
33    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579537   
34    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579538   
35    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579539   
36    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579540   
37    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579541   
38   demo                                    994 W 24th Demo       579550   
39   game                                         Sky Trader       579560   
40   game                                 The Source of Evil       579580   
41   demo                           Elephant Express VR Demo       579600   
43   game                        The Body VR: Anatomy Viewer       579620   
45   game                     liquivid Video Fisheye Removal       579640   
46    dlc                              Root Letter - Artbook       579650   
50   game                                           Neverout       579720   
51    dlc                            Phoning Home Soundtrack       579730   
52    dlc              2Dark Official Soundtrack and Artbook       579740   
53    dlc                        Cavern escape - Soundtrack.       579750   
54   game                    The Journey Down: Chapter Three       579760   
55   game                                   Mental Asylum VR       579780   
56    dlc         Fantasy Grounds - Townsfolk 2 (Token Pack)       579790   
57   game                              Robinson: The Journey       579820   
5

In [592]:
# convert release_data to a date, if 'coming_soon==True' set a flag for not release? maybe a new column?

app_df_cleaned_9 = app_df_cleaned_8.copy()

s = app_df_cleaned_9['release_date'].apply(pd.Series)
s['date'] = pd.to_datetime(s['date'], errors='coerce')

app_df_cleaned_9 = pd.concat([app_df_cleaned_9, s], axis=1)
app_df_cleaned_9.drop(axis=1, columns='release_date', inplace=True)
app_df_cleaned_9.rename(columns={'date': 'release_date'}, inplace=True)
app_df_cleaned_9.head()


type                                       name  steam_appid  required_age  \
0  game                                   Swatcher       579920             0   
1   dlc  Secret World Legends: Supernatural Bundle       579930             0   
2  game                        Race for the Galaxy       579940             0   
4  demo                         Don't Mess Up Demo       579970             0   
5  game                                  Lost Eden       579980             0   

   is_free                               detailed_description  \
0    False  Swatcher is a color palette creation tool with...   
1    False  <h1>Secret World Legends</h1><p>Secret World L...   
2    False  Explore, Develop, Settle, Trade, Consume, or P...   
4     True  Don't Mess Up is a collection of VR minigames ...   
5    False  From the makers of Dune™ and Megarace™<br>Lost...   

                                      about_the_game  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Develop, Settle, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  From the makers of Dune™ and Megarace™<br>Lost...   

                                   short_description  \
0  Swatcher is a color palette creation tool with...   
1  You’ve heeded the call; now explore the possib...   
2  Explore, Settle, Develop, Trade, Consume, or P...   
4  Don't Mess Up is a collection of VR minigames ...   
5  An adventure-strategy game in a world never be...   

                                 supported_languages  \
0                                            English   
1  English<strong>*</strong>, French<strong>*</st...   
2                                            English   
4  English<strong>*</strong><br><strong>*</strong...   
5  English<strong>*</strong>, Italian, Spanish - ...   

                           website            developers  \
0           http://swatcherapp.com        [Frozen Flame]   
1  https://secretworldlegends.com/              [Funcom]   
2      http://templegatesgames.com  [Temple Gates Games]   
4                             None            [OKatBest]   
5         http://www.interplay.com    [Cryo Interactive]   

             publishers  packages  \
0        [Frozen Flame]  [148602]   
1              [Funcom]  [148605]   
2  [Temple Gates Games]  [148608]   
4            [OKatBest]       NaN   
5           [Interplay]  [148620]   

                                      package_groups  \
0  [{'name': 'default', 'title': 'Buy Swatcher', ...   
1  [{'name': 'default', 'title': 'Buy Secret Worl...   
2  [{'name': 'default', 'title': 'Buy Race for th...   
4                                                 []   
5  [{'name': 'default', 'title': 'Buy Lost Eden',...   

                                            fullgame  \
0                                                NaN   
1  {'appid': '215280', 'name': 'Secret World Lege...   
2                                                NaN   
4       {'appid': '575170', 'name': 'Don't Mess Up'}   
5                                                NaN   

                                          categories  \
0                                                NaN   
1  [{'id': 1, 'description': 'Multi-player'}, {'i...   
2  [{'id': 2, 'description': 'Single-player'}, {'...   
4  [{'id': 2, 'description': 'Single-player'}, {'...   
5        [{'id': 2, 'description': 'Single-player'}]   

                        dlc  controller_support achievements metacritic demos  \
0                       NaN               False          NaN        NaN   NaN   
1                       NaN               False          NaN        NaN   NaN   
2  [647070, 647071, 762070]               False          NaN        NaN   NaN   
4                       NaN               False          NaN        NaN   NaN   
5                       NaN               False          NaN        NaN   NaN   

  drm_notice ext_user_account_no

In [593]:
# how long is reviews column - most have none - can maybe trash this

app_df_cleaned_10 = app_df_cleaned_9.copy()
# print(app_df_cleaned_10.info())
# app_df_cleaned_10.drop(columns='reviews', inplace=True)
# print(app_df_cleaned_10.info())

# note that i already added reviews column to list of columns to delete in the begining


In [594]:
# - pull out the appid of the fullgame column so we can link them if needed
# - demos is link to appids for game demo - probably do care about this - maybe convert to a true/false for demo existing? maybe a column for nbr demos?
# - dlc is a list of appids for dlc - lets add a column for the dlc count
app_df_cleaned_11 = app_df_cleaned_10.copy()

fullgame = app_df_cleaned_11['fullgame']
s = fullgame.apply(pd.Series)
s.drop(axis=1, columns=['name', 0], inplace=True)
s.rename(columns={'appid': 'fullgame_appid'}, inplace=True)
app_df_cleaned_11 = pd.concat([app_df_cleaned_11, s], axis=1)

# there seems to be only 1 demo in the subset i pulled so we'll just show that one demo id instead of the dict
s = app_df_cleaned_11['demos'].apply(pd.Series)
y = pd.Series()
s['demo_appid'] = s[0].apply(lambda x: str(x['appid']) if not pd.isnull(x) else np.nan)
app_df_cleaned_11 = pd.concat([app_df_cleaned_11, s['demo_appid']], axis=1)

# let's keep the list of dlc appid incase we want them
app_df_cleaned_11['dlc_count'] = app_df_cleaned_11['dlc'].apply(lambda x: len(x) if type(x) == list else 0)


app_df_cleaned_11.drop(columns=['fullgame', 'demos'], inplace=True)


/Users/emily/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:14: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  


In [595]:
# split out categories column so they can be easily accessed
# this is copy/paste from the genre conversion
# need to revisit this for if there are still just 14 columns when we get more data - maybe add some logic to catch it?

app_df_cleaned_12 = app_df_cleaned_11.copy()

s = app_df_cleaned_12['categories'].apply(pd.Series)
y = s[0].append([s[1],s[2],s[3],s[4],s[5],s[6],s[7],s[8],s[9],s[10],s[11],s[12],s[13],s[14]],ignore_index=True).dropna()
#split out dict to seprate columns
y
z = y.apply(pd.Series)
z = z.drop_duplicates(subset=['id','description'], keep="first")

# create a column for each unique category and then fill those columns in the df with bools
for index, row in z.iterrows():
    no_space_name = row['description'].replace(" ", "_")
    new_col = 'category_{}'.format(no_space_name)
    app_df_cleaned_12[new_col] = False

for index, row in app_df_cleaned_12.iterrows():
    if type(row['categories']) == float:
        continue
    for item in row['categories']:
        no_space_name = item['description'].replace(" ", "_")
        new_name = 'category_{}'.format(no_space_name)
        app_df_cleaned_12.at[index, new_name] = True

app_df_cleaned_12.drop(columns='categories', inplace=True)
app_df_cleaned_12


type                                               name  steam_appid  \
0    game                                           Swatcher       579920   
1     dlc          Secret World Legends: Supernatural Bundle       579930   
2    game                                Race for the Galaxy       579940   
4    demo                                 Don't Mess Up Demo       579970   
5    game                                          Lost Eden       579980   
6     dlc                             TEKKEN 7 - Season Pass       580020   
7    game                                            Formata       580040   
8     dlc            RPG Maker MV - Elemental Dungeons Tiles       580050   
9     dlc                   RPG Maker MV - Future Steam Punk       580051   
10   game                                     Cut Cut Buffet       580060   
11   demo                                      Frog Hop Demo       580070   
12    dlc         RPG Maker MV - Add-on Vol.3: Train Tileset       580080   
13    dlc   RPG Maker MV - Add-on Vol.4: Kid Generator Parts       580081   
14    dlc                Darkest Dungeon®: The Crimson Court       580100   
15   demo                                  Abyssal Zone Demo       580110   
16    dlc                                Westboro Soundtrack       580120   
17    dlc                                  Laraan SoundTrack       580160   
18   game                                 My Lovely Daughter       580170   
19   game               Yonder: The Cloud Catcher Chronicles       580200   
20    dlc                                  真恋～寄语枫秋～特色作曲家（秋石）       580210   
21    dlc       Fantasy Grounds - More Monsters (Token Pack)       580240   
22   demo                     Crypt of the Serpent King Demo       580250   
24    dlc                 Fantasy Grounds - Black Magic (5E)       580290   
25   game                                 Super Stone Legacy       580300   
26   game                                           Ashworld       580320   
27    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579531   
28    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579532   
29    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579533   
30    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579534   
31    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579535   
32    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579536   
33    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579537   
34    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579538   
35    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579539   
36    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579540   
37    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579541   
38   demo                                    994 W 24th Demo       579550   
39   game                                         Sky Trader       579560   
40   game                                 The Source of Evil       579580   
41   demo                           Elephant Express VR Demo       579600   
43   game                        The Body VR: Anatomy Viewer       579620   
45   game                     liquivid Video Fisheye Removal       579640   
46    dlc                              Root Letter - Artbook       579650   
50   game                                           Neverout       579720   
51    dlc                            Phoning Home Soundtrack       579730   
52    dlc              2Dark Official Soundtrack and Artbook       579740   
53    dlc                        Cavern escape - Soundtrack.       579750   
54   game                    The Journey Down: Chapter Three       579760   
55   game                                   Mental Asylum VR       579780   
56    dlc         Fantasy Grounds - Townsfolk 2 (Token Pack)       579790   
57   game                              Robinson: The Journey       579820   
5

In [596]:
# what's metacritic?

app_df_cleaned_13 = app_df_cleaned_12.copy()


s = app_df_cleaned_13['metacritic'].apply(pd.Series)
s.drop(columns=[0,'url'], inplace=True)
s.rename(columns={'score': 'metacritic_score'}, inplace=True)

app_df_cleaned_13 = pd.concat([app_df_cleaned_13, s], axis=1)
app_df_cleaned_13.drop(axis=1, columns='metacritic', inplace=True)
app_df_cleaned_13

type                                               name  steam_appid  \
0    game                                           Swatcher       579920   
1     dlc          Secret World Legends: Supernatural Bundle       579930   
2    game                                Race for the Galaxy       579940   
4    demo                                 Don't Mess Up Demo       579970   
5    game                                          Lost Eden       579980   
6     dlc                             TEKKEN 7 - Season Pass       580020   
7    game                                            Formata       580040   
8     dlc            RPG Maker MV - Elemental Dungeons Tiles       580050   
9     dlc                   RPG Maker MV - Future Steam Punk       580051   
10   game                                     Cut Cut Buffet       580060   
11   demo                                      Frog Hop Demo       580070   
12    dlc         RPG Maker MV - Add-on Vol.3: Train Tileset       580080   
13    dlc   RPG Maker MV - Add-on Vol.4: Kid Generator Parts       580081   
14    dlc                Darkest Dungeon®: The Crimson Court       580100   
15   demo                                  Abyssal Zone Demo       580110   
16    dlc                                Westboro Soundtrack       580120   
17    dlc                                  Laraan SoundTrack       580160   
18   game                                 My Lovely Daughter       580170   
19   game               Yonder: The Cloud Catcher Chronicles       580200   
20    dlc                                  真恋～寄语枫秋～特色作曲家（秋石）       580210   
21    dlc       Fantasy Grounds - More Monsters (Token Pack)       580240   
22   demo                     Crypt of the Serpent King Demo       580250   
24    dlc                 Fantasy Grounds - Black Magic (5E)       580290   
25   game                                 Super Stone Legacy       580300   
26   game                                           Ashworld       580320   
27    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579531   
28    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579532   
29    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579533   
30    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579534   
31    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579535   
32    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579536   
33    dlc  RTK13WPK - Tie-up with Kihachiro Kawamoto's "S...       579537   
34    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579538   
35    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579539   
36    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579540   
37    dlc  RTK13WPK - Fan selected Re-Releases Officer Gr...       579541   
38   demo                                    994 W 24th Demo       579550   
39   game                                         Sky Trader       579560   
40   game                                 The Source of Evil       579580   
41   demo                           Elephant Express VR Demo       579600   
43   game                        The Body VR: Anatomy Viewer       579620   
45   game                     liquivid Video Fisheye Removal       579640   
46    dlc                              Root Letter - Artbook       579650   
50   game                                           Neverout       579720   
51    dlc                            Phoning Home Soundtrack       579730   
52    dlc              2Dark Official Soundtrack and Artbook       579740   
53    dlc                        Cavern escape - Soundtrack.       579750   
54   game                    The Journey Down: Chapter Three       579760   
55   game                                   Mental Asylum VR       579780   
56    dlc         Fantasy Grounds - Townsfolk 2 (Token Pack)       579790   
57   game                              Robinson: The Journey       579820   
5

In [597]:
# content descriptors - relates to age restriction - decided to drop it and added it to master drop list
app_df_cleaned_14 = app_df_cleaned_13.copy()

# app_df_cleaned_14 = app_df_cleaned_14.drop(columns='content_descriptors', axis=1)
app_df_cleaned_14.info()


<class 'pandas.core.frame.DataFrame'>
Int64Index: 697 entries, 0 to 942
Data columns (total 96 columns):
 #   Column                               Non-Null Count  Dtype         
---  ------                               --------------  -----         
 0   type                                 697 non-null    object        
 1   name                                 697 non-null    object        
 2   steam_appid                          697 non-null    int64         
 3   required_age                         697 non-null    int64         
 4   is_free                              697 non-null    bool          
 5   detailed_description                 697 non-null    object        
 6   about_the_game                       697 non-null    object        
 7   short_description                    697 non-null    object        
 8   supported_languages                  694 non-null    object        
 9   website                              503 non-null    object        
 10  developers    

In [598]:
# what's achievements - it's the number of achievments avilable for the game
app_df_cleaned_15 = app_df_cleaned_14.copy()

ach = app_df_cleaned_15['achievements'].dropna()
ach = ach.apply(pd.Series)
ach.drop(columns='highlighted', inplace=True)
ach.rename(columns={"total": "achievement_count"}, inplace=True)

app_df_cleaned_15 = pd.concat([app_df_cleaned_15, ach], axis=1)
app_df_cleaned_15.drop(axis=1, columns='achievements', inplace=True)
print(app_df_cleaned_15['achievement_count'].unique())


# app_df_cleaned_xxx = app_df_cleaned_14.copy()
# df_clean = pd.concat([app_df_cleaned_xxx, app_df_cleaned_xxx['achievements'].apply(pd.Series)], axis=1)
# df_clean.drop(axis=1, columns=[0, 'achievements', 'highlighted'], inplace=True)
# df_clean.rename(columns={"total": "achievement_count"}, inplace=True)
# print(df_clean['achievement_count'].unique())







[      nan 3.000e+01 5.000e+01 3.800e+01 1.700e+01 2.300e+01 8.000e+00
 7.000e+00 2.500e+01 1.400e+01 2.100e+01 1.300e+01 3.000e+00 5.000e+00
 2.000e+00 3.400e+01 2.900e+01 2.600e+01 6.600e+01 8.400e+01 2.200e+01
 1.600e+01 1.000e+01 1.200e+01 2.000e+01 0.000e+00 1.000e+00 5.500e+01
 3.700e+01 1.900e+01 6.000e+00 4.600e+01 9.100e+01 2.400e+01 2.800e+01
 2.700e+01 3.300e+01 4.000e+00 1.500e+01 6.100e+01 3.100e+01 1.100e+01
 4.100e+01 1.800e+01 9.200e+01 1.708e+03 1.010e+02 5.700e+01 4.300e+01
 5.100e+01 3.900e+01 9.000e+00 3.500e+01 9.821e+03 3.200e+01 4.400e+01
 1.540e+02 7.000e+01 9.600e+01 4.700e+01 6.300e+01 6.000e+01 5.600e+01
 8.000e+01 7.400e+01 2.940e+02]


In [599]:
# define the packages and package_group column? list of a numeric?
app_df_cleaned_16 = app_df_cleaned_15.copy()
s = app_df_cleaned_16[['packages', 'package_groups']]

s['len'] = s['packages']
s

# still not sure what this is but not high priority to find out now - leave as is until i fugure it out

/Users/emily/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


packages  \
0                    [148602]   
1                    [148605]   
2                    [148608]   
4                         NaN   
5                    [148620]   
6                    [148631]   
7                    [148644]   
8                         NaN   
9                    [148651]   
10                   [148654]   
11                        NaN   
12                   [148662]   
13                   [148665]   
14                   [148671]   
15                        NaN   
16                   [148677]   
17                   [148689]   
18                   [148692]   
19                   [148707]   
20                        NaN   
21                   [148727]   
22                        NaN   
24                   [148752]   
25                   [148755]   
26                   [148761]   
27                        NaN   
28                        NaN   
29                        NaN   
30                        NaN   
31                        NaN   
32                        NaN   
33                        NaN   
34                        NaN   
35                        NaN   
36                        NaN   
37                        NaN   
38                        NaN   
39                        NaN   
40                   [148480]   
41                        NaN   
43                        NaN   
45                   [148500]   
46                   [148503]   
50                   [148533]   
51                   [148536]   
52                   [148539]   
53           [148542, 307430]   
54                   [148545]   
55                   [148551]   
56                   [148554]   
57                   [148562]   
58                   [148577]   
59                   [148580]   
60                   [148587]   
83                        NaN   
101                  [148185]   
102          [148188, 240227]   
127                  [148266]   
132                       NaN   
133                  [147972]   
134                  [147975]   
135                  [147978]   
136                  [147983]   
137                  [147994]   
138                  [148001]   
139                  [148004]   
140                  [148007]   
141                  [148023]   
142                  [148029]   
143                  [148095]   
144                  [147805]   
145                  [147809]   
147                  [147824]   
148                  [147833]   
149                       NaN   
150                  [147842]   
151                  [147851]   
152                       NaN   
153                  [147860]   
154                       NaN   
155                  [147872]   
156                  [147875]   
157                  [147878]   
158                  [147881]   
159                  [147888]   
160          [147891, 352570]   
161                       NaN   
162                  [147903]   
163          [147906, 183896]   
164                  [147915]   
165                  [147924]   
166                  [147927]   
167                       NaN   
168                       NaN   
169                       NaN   
170                  [147652]   
172                       NaN   
173                  [147670]   
174                  [147677]   
175                  [147680]   
176                  [147685]   
177                  [147691]   
178                  [147694]   
179                  [147697]   
186                  [310025]   
187                  [147721]   
188                  [147724]   
189                       NaN   
190                  [147738]   
191                  [147744]   
193                       NaN   
197                  [147773]   
198                  [147782]   
200                  [147800]   
201                       NaN   
203                  [147499]   
204                       NaN   
205                  [147505]   
207                  [147527]   
208                  [147531]   
209                  [147537

In [600]:
# write results out to a csv so I can compare it to the results when I consolidate all teh code into something i can rerun and easily tweak and reduce clutter

# app_df_cleaned_16.to_csv('initial_processed.csv', index=False) 

# make data i started with available to other notebooks
# app_df_expanded.to_csv('initial_preprocessed.csv', index=False) 
